In [1]:
import open3d as o3d
import numpy as np

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


In [43]:
# We will be reading in this mesh using the Open3D `read_t`
cup_path = "/viscam/projects/fluid-manip/FluidLab/fluidlab/assets/meshes/processed/glass-glass_vis.obj"

In [73]:
mesh = o3d.geometry.TriangleMesh.create_coordinate_frame()
fps_indices = np.load("/viscam/projects/fluid-manip/VGPL-Dynamics-Prior/data/data_Pouring/train/0/fps.npy")
particles = np.load("/viscam/projects/fluid-manip/VGPL-Dynamics-Prior/data/data_Pouring/train/0/x.npy", mmap_mode="r+")[:, :-1][:, fps_indices]
print(particles.shape)
grouping_info = np.load("/viscam/projects/fluid-manip/VGPL-Dynamics-Prior/data/data_Pouring/train/0/stat.npy")
print(len(grouping_info))
cup = o3d.io.read_triangle_mesh(cup_path)
cup_r = o3d.io.read_triangle_mesh(cup_path)
R = mesh.get_rotation_matrix_from_xyz((np.pi / 2, 0, 0))
# cup_r.rotate(R, center=(0,0,0))

(1000, 300, 3)
40604


In [74]:
grouping_info = grouping_info[fps_indices]

In [75]:
particles_last = particles[0]
indices_non_neg = np.where(np.any(particles_last != -100, axis=1))[0]
print(indices_non_neg)
p = particles_last[indices_non_neg]
grouping_info = grouping_info[indices_non_neg]
# particles = np.random.rand(300, 3)
pcd = o3d.geometry.PointCloud()
pcd.points = o3d.utility.Vector3dVector(p)
print(len(pcd.points))
print(cup_r.get_center())
cup_r = cup_r.translate(-1 * cup_r.get_center())
cup_r = cup_r.translate([0.63, 0.42, 0.5])
cup_r = cup_r.scale(1.2, [0.63, 0.42, 0.5])
cup_r.get_center()

[  0   1   2   3   4   5   6   7   8   9  10  11  12  13  14  15  16  17
  18  19  20  21  22  23  24  25  26  27  28  29  30  31  32  33  34  35
  36  37  38  39  40  41  42  43  44  45  46  47  48  49  50  51  52  53
  54  55  56  57  58  59  60  61  62  63  64  65  66  67  68  69  70  71
  72  73  74  75  76  77  78  79  80  81  82  83  84  85  86  87  88  89
  90  91  92  93  94  95  96  97  98  99 100 101 102 103 104 105 106 107
 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125
 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143
 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161
 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179
 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197
 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215
 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233
 234 235 236 237 238 239 240 241 242 243 244 245 24

array([0.63, 0.42, 0.5 ])

In [76]:
import copy
color_coffee = [15.0/255, 94.0/255, 156.0/255]
color_milk = [128.0/255, 128.0/255, 128.0/255]
# cup_r.vertex_colors = o3d.utility.Vector3dVector(vertex_colors)
colors = np.zeros((300, 3), dtype="float64")
colors[grouping_info == 0] = color_milk
# colors[:] = color_coffee
colors[grouping_info == 1] = color_coffee
# colors = colors[1:]
pcd.colors = o3d.utility.Vector3dVector(colors)

In [77]:
o3d.visualization.draw_plotly([cup_r, pcd])

In [47]:
import plotly.graph_objects as go
points = np.asarray(pcd.points)
colors = np.asarray(pcd.colors)

In [8]:
fig = go.Figure()
fig = go.Figure(data=go.Scatter3d(
    x=points[:, 0],
    y=points[:, 1],
    z=points[:, 2],
    mode='markers',
    marker=dict(
        size=2,  # Adjust the marker size as desired
        color=colors,
        opacity=1.0
    )
))